In [1]:
import numpy as np

In [2]:
def loadDataset():
    x_train = np.fromfile('data/train-images-idx3-ubyte', dtype=np.ubyte, offset=16).reshape(-1, 28, 28)
    y_train = np.fromfile('data/train-labels-idx1-ubyte', dtype=np.ubyte, offset=8).reshape(-1)
    x_test = np.fromfile('data/t10k-images-idx3-ubyte', dtype=np.ubyte, offset=16).reshape(-1, 28, 28)
    y_test = np.fromfile('data/t10k-labels-idx1-ubyte', dtype=np.ubyte, offset=8).reshape(-1)
    return x_train, y_train, x_test, y_test

In [3]:
def fit(x_train, y_train, mode):
    # P(t|X) = P(X|t)P(t)/P(X) = P(x1|t)P(x2|t)...P(t)/P(X)
    # prior: P(t)
    # pixelLikelihood: P(x1|t), P(x2|t), ...
    # mode: 0: discrete, else: continuous
    
    prior = np.bincount(y_train) / len(y_train) # (10,)
    
    if mode == 0: # discrete
        
        pixelLikelihood = np.ones((10, 28, 28, 32)) # (10, 28, 28, 32), initialized to 1 to avoid 0s

        for x, y in zip(x_train, y_train):
            for i in range(28):
                for j in range(28):
                    pixelLikelihood[y, i, j, x[i, j] // 8] += 1


        pixelLikelihood /= np.sum(pixelLikelihood, axis=3, keepdims=True)

        return pixelLikelihood, prior
    
    else: # continuous
        
        pixelGaussian = {'mu': np.zeros((10, 28, 28)), 'var': np.zeros((10, 28, 28))}

        for i in range(10):
            pixelGaussian['mu'][i] = np.mean(x_train[y_train == i], axis=0)
            pixelGaussian['var'][i] = np.maximum(1e2, np.var(x_train[y_train == i], axis=0)) # avoid 0
        
        return pixelGaussian, prior

In [4]:
def printImagination(pixelProb, mode):
    # pixelProb: pixel likelihood in discrete mode, pixel gaussian parameters in continuous mode
    # mode: 0: discrete, 1: continuous
    
    print('Imagination of numbers in Bayesian classifier:')
    
    for i in range(10):
        print(f'\n{i}:')
        for j in range(28):
            if mode == 0: # discrete
                print(*['1' if np.argmax(pixelProb[i, j, k]) >= 16 else '0' for k in range(28)])
            else: # continuous
                print(*['1' if pixelProb['mu'][i, j, k] >= 128 else '0' for k in range(28)])
    

In [5]:
def test(pixelProb, prior, x_test, y_test, mode):
    # P(t|X) = P(X|t)P(t)/P(X) = P(x1|t)P(x2|t)...P(t)/P(X)
    # pixelProb: pixel likelihood in discrete mode, pixel gaussian parameters in continuous mode
    # mode: 0: discrete, 1: continuous
    
    logNormalPdf = lambda mu, var, x: -0.5 * np.log(2 * np.pi * var) + -0.5 * (x - mu) ** 2 / var
    
    correct, total = 0, 0
    
    for x, y in zip(x_test, y_test):
        
        # calculate log[P(x1|t)P(x2|t)...P(t)]
        posterior = np.log(prior)
        
        for i in range(10):
            for j in range(28):
                for k in range(28):
                    if mode == 0: # discrete
                        posterior[i] += np.log(pixelProb[i, j, k, x[j, k] // 8])
                    else: # continuous
                        posterior[i] += logNormalPdf(pixelProb['mu'][i, j, k], pixelProb['var'][i, j, k], x[j, k])
        
        prediction = np.argmax(posterior)
        
        # normalized to sum to 1
        posterior /= np.sum(posterior)
        
        if prediction == y:
            correct += 1
        total += 1
        
        print('Postirior (in log scale):')
        for i in range(10):
            print(f'{i}: {posterior[i]}')
        
        print(f'Prediction: {prediction}, Ans: {y}\n')
        
    printImagination(pixelProb, mode)
    
    print(f'\nError rate: {1 - correct / total}')
    

In [6]:
def main(argv):
    _, mode, *_ = argv
    mode = int(mode)
    
    x_train, y_train, x_test, y_test = loadDataset()
    
    pixelProb, prior = fit(x_train, y_train, mode)
    test(pixelProb, prior, x_test, y_test, mode)
    
    return 0

In [7]:
main(['', 0])

Postirior (in log scale):
0: 0.11115533817604589
1: 0.11763260092591118
2: 0.10517186686202931
3: 0.100137502169675
4: 0.09389200359742099
5: 0.09755836271909257
6: 0.11442027192059406
7: 0.07444161841056393
8: 0.09952134045842094
9: 0.08606909476024607
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.100200409517963
1: 0.1070352761035449
2: 0.08332998753571914
3: 0.09034569728975578
4: 0.10877362309335535
5: 0.09252556976147994
6: 0.08965940269603626
7: 0.1189298263709533
8: 0.0963398173153031
9: 0.11286039031588922
Prediction: 2, Ans: 2

Postirior (in log scale):
0: 0.12847683719829553
1: 0.06386485811570505
2: 0.09868145466521333
3: 0.10061294868354335
4: 0.10342484486532438
5: 0.0967118427966981
6: 0.10335360293650774
7: 0.10144903732164526
8: 0.10041020791933995
9: 0.10301436549772738
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.07779623593480413
1: 0.14086686086543018
2: 0.09708059599688122
3: 0.09653935618761733
4: 0.10150694263616061
5: 0.09270337417119959
6: 0.09

Postirior (in log scale):
0: 0.13072792564759536
1: 0.07556632807834468
2: 0.10639273532143204
3: 0.09893835183234313
4: 0.09900690260949647
5: 0.09343715282835144
6: 0.10544826531202896
7: 0.09401062447523138
8: 0.10177249852937088
9: 0.09469921536580568
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.10832106248769975
1: 0.11785366505750323
2: 0.10164189719684648
3: 0.08103784774599634
4: 0.09868437597757304
5: 0.08687045745584311
6: 0.10677865621246412
7: 0.1061982418346831
8: 0.09405966289754764
9: 0.09855413313384323
Prediction: 3, Ans: 3

Postirior (in log scale):
0: 0.08723118195573099
1: 0.13331390609596527
2: 0.09303907272998847
3: 0.10720420852591851
4: 0.09071424931277706
5: 0.0918049918666768
6: 0.08754290075626482
7: 0.10661442096453899
8: 0.0998263903196864
9: 0.10270867747245273
Prediction: 0, Ans: 4

Postirior (in log scale):
0: 0.11248847250918312
1: 0.11042481412588082
2: 0.09547748935820845
3: 0.10023315439652915
4: 0.09720855306951472
5: 0.09780554689239254
6:

Postirior (in log scale):
0: 0.1087827100753103
1: 0.1248900789962719
2: 0.09743948996987076
3: 0.0989406950058304
4: 0.09170292279774424
5: 0.09799887970440055
6: 0.10550032776111358
7: 0.0865418765769708
8: 0.09549311160551698
9: 0.09270990750697056
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.125408444967972
1: 0.09903990814534146
2: 0.10744821457914389
3: 0.09655364997627053
4: 0.09253582281195502
5: 0.09143795487152773
6: 0.10236585996795325
7: 0.09876631724835451
8: 0.09700774795575477
9: 0.08943607947572686
Prediction: 9, Ans: 4

Postirior (in log scale):
0: 0.10182100170277814
1: 0.11677278014132965
2: 0.09254537208142338
3: 0.1002583873484133
4: 0.0952946122291377
5: 0.09880215727976045
6: 0.0937675782316675
7: 0.09929425765582486
8: 0.10057473035400594
9: 0.10086912297565907
Prediction: 2, Ans: 6

Postirior (in log scale):
0: 0.10587472586668929
1: 0.12467693589698717
2: 0.0970830883134014
3: 0.10692983128380588
4: 0.080946193556237
5: 0.09811878412791443
6: 0.103119

Postirior (in log scale):
0: 0.11403903398332864
1: 0.11311850414369858
2: 0.10083203672452161
3: 0.09591866488314472
4: 0.09546104128031419
5: 0.09642366624909399
6: 0.09974635107164714
7: 0.0953336952909683
8: 0.09437823698780323
9: 0.09474876938547958
Prediction: 8, Ans: 7

Postirior (in log scale):
0: 0.09511440652808645
1: 0.1182314243062324
2: 0.09252948430597072
3: 0.10194012095606478
4: 0.09891481293119084
5: 0.09210619651246156
6: 0.084016520321647
7: 0.11338325080604084
8: 0.0983893734183877
9: 0.10537440991391783
Prediction: 6, Ans: 6

Postirior (in log scale):
0: 0.11185036296730745
1: 0.13445132553568706
2: 0.09901483154525635
3: 0.10186626417283041
4: 0.0839584946426973
5: 0.09891034436906214
6: 0.100917830556009
7: 0.09199389874213
8: 0.0962137772229698
9: 0.08082287024605055
Prediction: 9, Ans: 9

Postirior (in log scale):
0: 0.10385879103704318
1: 0.11478810147559426
2: 0.09376597310777793
3: 0.10265206109910878
4: 0.09368940742277326
5: 0.09948889984233761
6: 0.087562

Postirior (in log scale):
0: 0.10239370210296489
1: 0.12953714037960554
2: 0.09408455243592544
3: 0.1029789863588365
4: 0.09435811811717608
5: 0.09558138803158509
6: 0.07645025859641494
7: 0.11103368377995365
8: 0.09538242112893464
9: 0.0981997490686031
Prediction: 6, Ans: 6

Postirior (in log scale):
0: 0.09463791009699782
1: 0.1295823944062304
2: 0.09054423888001127
3: 0.10123746560113793
4: 0.09651211006707558
5: 0.09282912378460766
6: 0.0774606792979787
7: 0.11754096050131882
8: 0.09436793849167971
9: 0.1052871788729622
Prediction: 6, Ans: 6

Postirior (in log scale):
0: 0.09307265047359868
1: 0.13024671070037575
2: 0.09493868582451756
3: 0.08553405419072277
4: 0.10595030078998594
5: 0.0841881768049887
6: 0.09294267473624146
7: 0.1164744101794311
8: 0.08982498239365827
9: 0.10682735390647988
Prediction: 5, Ans: 5

Postirior (in log scale):
0: 0.11167129643169656
1: 0.1250353366030358
2: 0.09016661861067533
3: 0.09928107745673245
4: 0.09163953994527735
5: 0.10276878523458738
6: 0.10

...

Postirior (in log scale):
0: 0.1234642748198536
1: 0.07215554155183937
2: 0.09076286037307615
3: 0.09927832096541554
4: 0.10188634564911604
5: 0.09570652131404228
6: 0.10985266935374109
7: 0.10863177141578506
8: 0.09084542489507448
9: 0.10741626966205631
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.09985400910845608
1: 0.12160067863942033
2: 0.10329461948883534
3: 0.10632081879309412
4: 0.09005111105644167
5: 0.09495788258835752
6: 0.10362605071729522
7: 0.09260409007858071
8: 0.0972573575895315
9: 0.0904333819399875
Prediction: 4, Ans: 9

Postirior (in log scale):
0: 0.10866495951412872
1: 0.10738644621621772
2: 0.09359162815528822
3: 0.10104742885579758
4: 0.09897293559017678
5: 0.09521701232646615
6: 0.10722802217109145
7: 0.09772651461173826
8: 0.09277156014735861
9: 0.09739349241173655
Prediction: 8, Ans: 3

Postirior (in log scale):
0: 0.10818204426014293
1: 0.10585530442362666
2: 0.0935359917507829
3: 0.09896790048303485
4: 0.09955475117694709
5: 0.09260125489423952
6: 

Postirior (in log scale):
0: 0.10835811101036415
1: 0.11835471719916393
2: 0.10818234812049643
3: 0.10492253176935404
4: 0.09258338708039127
5: 0.09615341011243382
6: 0.11277686898105226
7: 0.07737098493312011
8: 0.09818219970456578
9: 0.08311544108905816
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.1211774381598033
1: 0.09288500420797172
2: 0.10123018259715177
3: 0.10020504564474451
4: 0.09834494638801446
5: 0.09731714813258496
6: 0.11787425364013294
7: 0.08709497614110938
8: 0.09361034356602813
9: 0.09026066152245889
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.1186491260771393
1: 0.09591958786173495
2: 0.09843704327701465
3: 0.09469918942139728
4: 0.10242682633067657
5: 0.09668871162100252
6: 0.10174765454969951
7: 0.09842098394189855
8: 0.09412659866224574
9: 0.09888427825719093
Prediction: 8, Ans: 8

Postirior (in log scale):
0: 0.11588927874741586
1: 0.1228294897438356
2: 0.1024632732592385
3: 0.10714271890454012
4: 0.08113015762611343
5: 0.09887028334805709
6: 

Postirior (in log scale):
0: 0.10257993030388303
1: 0.12369698041285881
2: 0.09448728531075165
3: 0.0845418611335338
4: 0.10203889083695283
5: 0.08935505075985163
6: 0.11536203250487989
7: 0.10852759620333016
8: 0.07971839603345032
9: 0.09969197650050779
Prediction: 8, Ans: 8

Postirior (in log scale):
0: 0.10226843371406975
1: 0.13347751831473703
2: 0.10495146297948107
3: 0.10513786345766668
4: 0.08337131646798306
5: 0.0958283555810538
6: 0.10228461528567113
7: 0.09292034807530648
8: 0.09669000942160345
9: 0.08307007670242747
Prediction: 9, Ans: 9

Postirior (in log scale):
0: 0.0747034444474459
1: 0.13836227134103432
2: 0.09478993732594494
3: 0.09745937886039004
4: 0.09979820835677441
5: 0.08859120624673615
6: 0.09897316817178406
7: 0.11126989295697161
8: 0.09017320417977719
9: 0.10587928811314137
Prediction: 0, Ans: 0

Postirior (in log scale):
0: 0.12978916443559274
1: 0.06375301019845901
2: 0.09391804710558106
3: 0.09912910691909267
4: 0.10853488921999396
5: 0.09774637629563337
6:

0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

8:
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 1 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 1 1 1 1 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 0 0 0 0 

0

In [8]:
main(['', 1])

Postirior (in log scale):
0: 0.1082548609822742
1: 0.15812013840928185
2: 0.11027939846950105
3: 0.08804162895607963
4: 0.08700842254366428
5: 0.08635449794602264
6: 0.1311965187751837
7: 0.07010368494149334
8: 0.08784317873384512
9: 0.07279767024265432
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.0784777905507149
1: 0.13295833444874025
2: 0.057942607531013775
3: 0.0762865526396716
4: 0.10126852307070705
5: 0.07947139456193551
6: 0.07623310285539871
7: 0.16376865596139153
8: 0.09142092955275123
9: 0.14217210882767545
Prediction: 2, Ans: 2

Postirior (in log scale):
0: 0.10746588381074908
1: 0.08458194661041019
2: 0.09917488692985285
3: 0.09869560988281267
4: 0.09835890912029488
5: 0.09813338494101807
6: 0.09822255695806711
7: 0.11118702435792421
8: 0.09736622773107893
9: 0.10681356965779207
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.07134953233318173
1: 0.27591675806658994
2: 0.07774379281699806
3: 0.0775166368378031
4: 0.07983707556753963
5: 0.07613320042036877
6: 

Postirior (in log scale):
0: 0.08888418602192628
1: 0.17850866786871258
2: 0.0881659091687612
3: 0.07908894155890729
4: 0.08347021667706694
5: 0.08098193792411484
6: 0.12417019696265184
7: 0.09650103056006469
8: 0.08150135592396993
9: 0.09872755733382434
Prediction: 3, Ans: 3

Postirior (in log scale):
0: 0.06613643410792826
1: 0.27738690617411876
2: 0.0814246969851246
3: 0.09717337033456477
4: 0.06795074557278631
5: 0.06947186877260322
6: 0.0831006018514235
7: 0.09485598833243744
8: 0.07065281566685107
9: 0.09184657220216219
Prediction: 0, Ans: 4

Postirior (in log scale):
0: 0.1070663967058547
1: 0.1397223496422469
2: 0.1024669840083301
3: 0.08431676154981471
4: 0.08622386293368084
5: 0.08444534115419265
6: 0.14563628612034854
7: 0.08007241997118172
8: 0.08272843826331305
9: 0.08732115965103684
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.06792383231395085
1: 0.15614431142593832
2: 0.06669979410325709
3: 0.06884286071039876
4: 0.10378835020418703
5: 0.068935655706406
6: 0.09

Postirior (in log scale):
0: 0.09418439304753817
1: 0.09716212061674977
2: 0.08416241041398555
3: 0.08374297066121826
4: 0.10979149245367582
5: 0.08851829004278154
6: 0.09321386616267902
7: 0.13612416259605736
8: 0.08889026303092865
9: 0.12421003097438602
Prediction: 3, Ans: 3

Postirior (in log scale):
0: 0.10219330888452971
1: 0.22524601806759748
2: 0.0924142521862987
3: 0.07716501950645094
4: 0.08173869085787153
5: 0.08185255352062466
6: 0.1218188894428175
7: 0.061335860139963866
8: 0.08041155783052072
9: 0.07582384956332486
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.10661484075256566
1: 0.09804412138257583
2: 0.1025195874280431
3: 0.09873315491314509
4: 0.09737294072268256
5: 0.09845696621140898
6: 0.10289115131916737
7: 0.10178720887329921
8: 0.09807042298279374
9: 0.09550960541431845
Prediction: 9, Ans: 4

Postirior (in log scale):
0: 0.08446078348541906
1: 0.21271326243061667
2: 0.0761092108673569
3: 0.08125341499462023
4: 0.08878488413448614
5: 0.08601374109868773
6:

Postirior (in log scale):
0: 0.10877818390187545
1: 0.08547937533589951
2: 0.09534742769803409
3: 0.09380321858479485
4: 0.0970895220545303
5: 0.09348491868045426
6: 0.0942839838028179
7: 0.12548950474266707
8: 0.09184007805858202
9: 0.11440378714034453
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.08307851195310682
1: 0.2763871801969611
2: 0.07787195704204283
3: 0.0815273263052979
4: 0.07038377936890944
5: 0.07522715379417676
6: 0.08249523711576848
7: 0.09696401392280386
8: 0.07709180943545359
9: 0.07897303086547937
Prediction: 4, Ans: 4

Postirior (in log scale):
0: 0.10920090646628929
1: 0.0913857351355422
2: 0.10211643232570466
3: 0.0987983825362729
4: 0.09865493276685638
5: 0.0985414413598087
6: 0.10474753882851856
7: 0.09902405740755382
8: 0.09845457456483912
9: 0.09907599860861445
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.09252486218674794
1: 0.19663941842617882
2: 0.08392321103944703
3: 0.09247799756732654
4: 0.07979572251616338
5: 0.08660807634791795
6: 0.0

Postirior (in log scale):
0: 0.08962489397493047
1: 0.13847760230742975
2: 0.09318061891040931
3: 0.09112705029087464
4: 0.08309417802150607
5: 0.08142323971260672
6: 0.1138663636003098
7: 0.11880325928996467
8: 0.08201855584875958
9: 0.10838423804320906
Prediction: 5, Ans: 5

Postirior (in log scale):
0: 0.10809629198853439
1: 0.15993066799569886
2: 0.10402776755301571
3: 0.07981153914645076
4: 0.07955790491820372
5: 0.07864288530860027
6: 0.15561297181747277
7: 0.08102687904878522
8: 0.07574877703840828
9: 0.07754431518483003
Prediction: 8, Ans: 8

Postirior (in log scale):
0: 0.09496612286162803
1: 0.11493331350365274
2: 0.09734982287221872
3: 0.09228393145504489
4: 0.09009079991106239
5: 0.08669674285489964
6: 0.134213485677378
7: 0.10256588622082037
8: 0.08683451760989325
9: 0.10006537703340201
Prediction: 5, Ans: 5

Postirior (in log scale):
0: 0.08324046541135173
1: 0.21670120856021555
2: 0.07689542517974454
3: 0.07925551427236827
4: 0.08094173039121368
5: 0.07663393841531754
6:

...

Postirior (in log scale):
0: 0.1064507774592024
1: 0.08113644265694228
2: 0.09322951600606742
3: 0.09524813627100984
4: 0.09612194295353765
5: 0.09345962993445299
6: 0.1061807839214913
7: 0.12478758371976933
8: 0.09163273301120181
9: 0.11175245406632503
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.08145844674747427
1: 0.24238701501329243
2: 0.09501531303898124
3: 0.09068021991402912
4: 0.07780471829128535
5: 0.07568281797577149
6: 0.11184630775801489
7: 0.06780408743673098
8: 0.08462541158554383
9: 0.07269566223887643
Prediction: 7, Ans: 9

Postirior (in log scale):
0: 0.09039990984721682
1: 0.12064159477988201
2: 0.08372099466235235
3: 0.08480870469609945
4: 0.11169032938522212
5: 0.08355713046900422
6: 0.11285171295471672
7: 0.1155407799005785
8: 0.0841565303286064
9: 0.11263231297632159
Prediction: 5, Ans: 3

Postirior (in log scale):
0: 0.09219272453486752
1: 0.10452914522630517
2: 0.0887121669066396
3: 0.09275840541806848
4: 0.10238787853515793
5: 0.07471972122956164
6: 0

Postirior (in log scale):
0: 0.06924412824929965
1: 0.23430646288229542
2: 0.07247316469107191
3: 0.08402945092939641
4: 0.08549594073285752
5: 0.07598705125129182
6: 0.06919034053393167
7: 0.11852060482978534
8: 0.08020628476850851
9: 0.11054657113156179
Prediction: 6, Ans: 6

Postirior (in log scale):
0: 0.06137508022523899
1: 0.2644229659243008
2: 0.06037380610304924
3: 0.0674163672742118
4: 0.09836100106183197
5: 0.06289657871638243
6: 0.10694501695228897
7: 0.10359875508099899
8: 0.06409085345248756
9: 0.1105195752092094
Prediction: 2, Ans: 2

Postirior (in log scale):
0: 0.09371842650554042
1: 0.08004310748808043
2: 0.08791277531189892
3: 0.09232746371402435
4: 0.10049771122762552
5: 0.08644086759022597
6: 0.11324338540414701
7: 0.13439847600618418
8: 0.08624148284692856
9: 0.12517630390534448
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.10581104041391991
1: 0.0819868839408813
2: 0.09387140432767663
3: 0.09509690859455137
4: 0.09939603275440033
5: 0.09427959181529337
6: 

Postirior (in log scale):
0: 0.059815453884324354
1: 0.2982105788711766
2: 0.07256927920192731
3: 0.07767568143829684
4: 0.07383160828579326
5: 0.06854990453123411
6: 0.1047989471982755
7: 0.09377558764094837
8: 0.06837318403462304
9: 0.08239977491340068
Prediction: 0, Ans: 0

Postirior (in log scale):
0: 0.11080493807531543
1: 0.08427462082684849
2: 0.1007645686119232
3: 0.09755698762551514
4: 0.0979488235096613
5: 0.09733401559567008
6: 0.11849611753706119
7: 0.10185133448538337
8: 0.09599100357281912
9: 0.09497759015980266
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.0984914407070988
1: 0.14089069210766075
2: 0.09127361233954041
3: 0.08917086821863889
4: 0.09032049389832845
5: 0.0889335998373439
6: 0.1285147833219959
7: 0.09812953474901769
8: 0.08611265118802733
9: 0.08816232363234787
Prediction: 8, Ans: 2

Postirior (in log scale):
0: 0.10084979471384063
1: 0.13812742087781346
2: 0.09326466824782689
3: 0.08898737178539198
4: 0.09660312402636098
5: 0.08862720961447398
6: 0.

0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 1 1 1 1 1 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 1 1 1 0 0 1 1 1 1 1 1 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 0 0 0 1 1 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 0 0 0 1 1 1 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 0 0 1 1 1 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

7:
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

0

In [ ]:
if __name__ == '__main__':
    import sys
    sys.exit(main(sys.argv))